In [1]:
import csv
import community
import pandas as pd
import networkx as nx
import math
import matplotlib.pyplot as plt
import pickle
import requests
import sys
from bs4 import BeautifulSoup
import re
import os

In [2]:
#transform resumption token into appropriate string: https://www.openarchives.org/OAI/openarchivesprotocol.html#HTTPRequestFormat
def getGoodToken(totalstring):
    result = totalstring.replace(' ', '%20')
    return result;

## Retrieving EC funded publications from OpenAire

In [13]:
print getGoodToken('272470|oaf|* AND (resulttypeid exact "publication" and funder exact "EC")|101000|5beec22045e3121cdfbc5abf|false|ECPublications')

272470|oaf|*%20AND%20(resulttypeid%20exact%20"publication"%20and%20funder%20exact%20"EC")|101000|5beec22045e3121cdfbc5abf|false|ECPublications


In [17]:
#takes a request url, retrieves a soup, saves a file for that soup, returns resumption token
def getIteration(url, session, directory):
    resp = session.get(url)
    soup = BeautifulSoup(resp.content, 'lxml')
    nexttoken = soup.find(re.compile("^oai:resumptiontoken"))
    filename = directory + 'soup' + str(nexttoken['cursor']) + '.txt'
    with open(filename, 'w') as f: 
        f.write(str(soup))
    return getGoodToken(nexttoken.text);

In [ ]:
#main loop
session = requests.session()
session.keep_alive = False
#for starting from scratch
#url = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&metadataPrefix=oaf&set=ECPublications'
#for continuing from the last resumption token
url = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=272470|oaf|*%20AND%20(resulttypeid%20exact%20"publication"%20and%20funder%20exact%20"EC")|101000|5beec22045e3121cdfbc5abf|false|ECPublications'
obtainedtoken = getIteration('./pubsoups/', url, session)
print obtainedtoken
for i in range(0, 280):
    url = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=' + obtainedtoken
    obtainedtoken = getIteration(url, session)
    print obtainedtoken

In [ ]:
#get the last one
respec = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=272470|oaf|*%20AND%20(resulttypeid%20exact%20"publication"%20and%20funder%20exact%20"EC")|272000|5beeca85bc99e50cd0f4fb35|false|ECPublications')
soupec = BeautifulSoup(respec.content, 'lxml')
soupec

## Retrieving all datasets from OpenAire

## Retrieving projects from OpenAire (semi manual)

In [ ]:
#this piece has to be run MANUALLY in pieces of 10 requests, due to memory limitations
#first uncomment initial request, set the name of the first file, run RETRIEVAL cell, save to file with cell SAVEFILE, restart kernell
#this is initial request
#respec = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&metadataPrefix=oaf&set=ECProjects')
#this request starts from specified resumptionToken
respec = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=45444|oaf|*%20AND%20(oaftype%20exact%20"project"%20and%20funder%20exact%20"EC")|43000|5beec7af45e3122ba28b4ee1|false|ECProjects')
soupec = BeautifulSoup(respec.content, 'lxml')
soups = list()
soups.append(soupec)
#first file name of retrieved 10 files - number should indicate the cursor position
f = open('soups42000.txt', 'a')
f.write(str(soupec))
f.close()

In [ ]:
#RETRIEVAL CELL
session = requests.session()
session.keep_alive = False
for i in range(0, 10):
    restoken = soups[len(soups)-1].find(re.compile("^oai:resumptiontoken"))
    print restoken
    if 'None' not in restoken.text:
        newtoken = getGoodToken(restoken.text)
        #newtoken='45444|oaf|*%20AND%20(oaftype%20exact%20"project"%20and%20funder%20exact%20"EC")|16000|5beec01edc92c52bf75a1792|false|ECProjects'
        requestring = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=' + newtoken
        print requestring
        resploop = session.get(requestring)
        souploop = BeautifulSoup(resploop.content, 'lxml')
        filename = 'soup' + str(restoken['cursor']) + '.txt'
        print filename
        f = open(filename, 'a')
        f.write(str(souploop))
        f.close()
        soups.append(souploop)
        print len(soups)
    else:
        print "no restoken"

In [ ]:
#SAVEFILE CELL
f = open('soupsfifty.txt', 'a')
f.write(str(soups))
f.close()

In [26]:
#get first, cursor 0
respec = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&metadataPrefix=oaf&set=ECProjects')
soupec = BeautifulSoup(respec.content, 'lxml')
soupec

<?xml version="1.0" encoding="UTF-8"?><html><body><oai:oai-pmh xmlns:oai="http://www.openarchives.org/OAI/2.0/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemalocation="http://www.openarchives.org/OAI/2.0/\n         http://www.openarchives.org/OAI/2.0/OAI-PMH.xsd">\n<oai:responsedate>2018-11-28T16:04:27Z</oai:responsedate>\n<oai:request metadataprefix="oaf" set="ECProjects" verb="ListRecords">http://api.openaire.eu/oai_pmh</oai:request>\n<oai:listrecords>\n<oai:record>\n<oai:header>\n<oai:identifier>oai:dnet:corda_______::064c125691aea6c77de63f7326b49291</oai:identifier>\n<oai:datestamp>2018-08-07T00:00:00Z</oai:datestamp>\n<oai:setspec>ECProjects</oai:setspec>\n<oai:setspec>CORDA_-_COmmon_Research_DAta_Warehouse</oai:setspec>\n</oai:header>\n<oai:metadata>\n<oaf:entity xmlns:oaf="http://namespace.openaire.eu/oaf" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemalocation="http://namespace.openaire.eu/oaf https://www.openaire.eu/schema/1.0/oaf-1.0.xsd">\n

## Retrieve grantIDs with dates from saved soupfiles

In [21]:
#takes a filename with soup inside, retrives grantIDs and respective date
def getGrantListFromFile(filename):
    grantlist = list()
    with open(filename) as file:  
        #restoken = file.readlines()[-2]
        #print restoken
        tempstr = file.read()
        #print tempstr
        soup = BeautifulSoup(tempstr, 'lxml')
        grantIDtags = soup.find_all('code')
        for grantID in grantIDtags:
            #print grantID
            grantIDdate = 'not available'
            for sibling in grantID.previous_siblings:
                if sibling.name == 'startdate':
                    grantIDdate = sibling.text #need to parse the date
            for sibling in grantID.next_siblings:
                if sibling.name == 'startdate':
                    grantIDdate = sibling.text #need to parse the date
            grantlist.append([grantID.text,grantIDdate])
            #[grantID.text] = grantIDdate
    return grantlist
    #print len(grantdict)
    #print grantdict

In [22]:
#test cell
getGrantListFromFile('./soups/soup1000first.txt')

[[u'333806', u'2013-05-01'],
 [u'247657', u'2010-11-01'],
 [u'327546', u'2013-03-01'],
 [u'294231', u'2011-09-01'],
 [u'331370', u'2013-10-01'],
 [u'608957', u'2013-06-01'],
 [u'226532', u'2009-01-01'],
 [u'226548', u'2009-05-01'],
 [u'291834', u'2012-04-01'],
 [u'624968', u'2014-10-01'],
 [u'237253', u'2009-06-01'],
 [u'605728', u'2014-03-01'],
 [u'294665', u'2012-07-01'],
 [u'285533', u'2012-09-01'],
 [u'618548', u'2013-09-01'],
 [u'254044', u'2010-07-01'],
 [u'286927', u'2011-10-01'],
 [u'258063', u'2010-10-01'],
 [u'274602', u'2011-05-09'],
 [u'274690', u'2011-04-01'],
 [u'272289', u'2012-01-01'],
 [u'623809', u'2014-03-01'],
 [u'602295', u'2013-11-01'],
 [u'267922', u'2011-04-01'],
 [u'219605', u'2009-04-01'],
 [u'218815', u'2009-01-01'],
 [u'249390', u'2010-05-01'],
 [u'325780', u''],
 [u'236156', u'2009-03-01'],
 [u'282280', u'2012-01-01'],
 [u'289085', u'2012-01-01'],
 [u'228589', u'2009-09-01'],
 [u'260699', u'2010-12-01'],
 [u'218516', u'2009-02-01'],
 [u'789573', u'2019-06-0

In [27]:
#construct an overall dictionary where each grantID has a date or n/a
directory = './soups/'
totalgrantlist = list()
for filename in os.listdir(directory):
    print filename
    templist = getGrantListFromFile(directory + filename)
    totalgrantlist = totalgrantlist + templist
    print len(totalgrantlist)

soup0first.txt
1000
soup1000.txt
2000
soup10000.txt
3000
soup11000.txt
4000
soup12000.txt
5000
soup13000.txt
6000
soup14000.txt
7000
soup15000.txt
8000
soup16000.txt
9000
soup17000.txt
10000
soup18000.txt
11000
soup19000.txt
12000
soup2000.txt
13000
soup20000.txt
14000
soup21000.txt
15000
soup22000.txt
16000
soup23000.txt
17000
soup24000.txt
18000
soup25000.txt
19000
soup26000.txt
20000
soup27000.txt
21000
soup28000.txt
22000
soup29000.txt
23000
soup3000.txt
24000
soup30000.txt
25000
soup31000.txt
26000
soup32000.txt
27000
soup33000.txt
28000
soup34000.txt
29000
soup35000.txt
30000
soup36000.txt
31000
soup37000.txt
32000
soup38000.txt
33000
soup39000.txt
34000
soup4000.txt
35000
soup40000.txt
36000
soup41000.txt
37000
soup42000.txt
38000
soup43000.txt
39000
soup44000.txt
40000
soup44000last.txt
40444
soup5000.txt
41444
soup6000.txt
42444
soup7000.txt
43444
soup8000.txt
44444
soup9000.txt
45444


In [25]:
print totalgrantlist

[[u'273010', u'2012-06-06'], [u'295231', u'2012-01-01'], [u'619120', u'2013-12-01'], [u'252343', u'2011-04-27'], [u'618969', u'2014-09-01'], [u'303799', u'2012-04-01'], [u'284437', u'2012-01-16'], [u'315282', u'2012-12-01'], [u'336679', u'2014-03-01'], [u'276998', u'2011-04-01'], [u'200265', u'2007-10-01'], [u'624496', u'2015-07-01'], [u'327581', u'2013-06-01'], [u'236311', u'2010-02-01'], [u'240795', u'2010-05-01'], [u'249142', u'2010-01-01'], [u'253063', u'2010-05-03'], [u'284529', u'2011-09-01'], [u'279369', u'2012-01-01'], [u'217346', u'2008-04-01'], [u'295264', u'2012-04-01'], [u'291201', u'2012-07-01'], [u'288102', u'2011-10-01'], [u'296423', u'2012-05-01'], [u'605658', u'2014-01-01'], [u'234303', u'2009-11-01'], [u'257626', u'2010-10-01'], [u'616480', u'2015-01-01'], [u'201751', u'2007-10-01'], [u'260911', u'2011-02-01'], [u'298494', u'2013-01-01'], [u'221823', u'2008-07-01'], [u'240185', u'2010-04-01'], [u'262147', u'2010-01-01'], [u'230837', u'2009-02-15'], [u'641463', u'2014-

In [30]:
#only used when saving the grantlist
#with open('totalgrantlist.txt', 'w') as f: 
#    f.write(str(totalgrantlist))
pickle_out = open("totalgrantlist.pickle","wb")
pickle.dump(totalgrantlist, pickle_out)
pickle_out.close()

In [ ]:
#save for later use - commented out to avoid overwriting
'''f = open('totalgrantdict.txt', 'a')
f.write(str(totalgrantdict))
f.close()'''

In [ ]:
#data notes:
'''Zenodo: 
- we take EC funded outputs from Zenodo
- we take relations only with 'grantAgreement'
OpenAire:
- retrieve only EC funded projects: 45444 projects
- retrieve only EC funded publications: 272 000 pubs
- remove publications with empty "dateofacceptance" tag
- remove publications with empty "pid" tag (indicates doi)
'''

In [ ]:
resp = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&metadataPrefix=oaf&set=ECPublications')
soup = BeautifulSoup(resp.content, 'lxml')
soup

In [ ]:
resp = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&metadataPrefix=oaf&set=openaire_data')
soup = BeautifulSoup(resp.content, 'lxml')
soup

## Trying Zenodo API

In [ ]:
#http://api.openaire.eu/search/publications
#resp = requests.get('http://api.openaire.eu/search/publications?size=100&hasProject=yes')
#http://api.openaire.eu/oai_pmh?verb=ListRecords&set=projects&metadataPrefix=oaf&resumptionToken=
#
resp = requests.get('https://zenodo.org/oai2d?verb=ListRecords&metadataPrefix=oai_dc&set=software')
soup = BeautifulSoup(resp.content, 'lxml')
soup

In [ ]:
#while page < max, use resumptiontokens to extract soups, then put all data into one big soup?
#resptwo = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=2544493|oaf|*%20AND%20oaftype%20exact%20"project"|1000|5beebb231e82123b9ba6b95d|false|projects')
#respzeno = requests.get('https://zenodo.org/oai2d?verb=ListRecords&set=user-ecfunded&metadataPrefix=oai_dc')
#soupzeno = BeautifulSoup(respzeno.content, 'lxml')
#get resumptiontoken
soups = list()
restoken = soup.find(re.compile("^resumptiontoken"))
print restoken.text
#while currecords < maxrecords:
for i in range(2000, 100000, 1000):
    print i,"/",100000
    #newtoken = getGoodToken(restoken.text)
    #print newtoken
    requestring = 'https://zenodo.org/oai2d?verb=ListRecords&resumptionToken=' + restoken.text
    print requestring
    resploop = requests.get(requestring)
    souploop = BeautifulSoup(resploop.content, 'lxml')
    soups.append(souploop)
    restoken = souploop.find(re.compile("^resumptiontoken"))
    #print currecords,"/",maxrecords

In [ ]:
#https://zenodo.org/oai2d?verb=ListRecords&resumptionToken=.eJwNzkFPgzAYgOH_8p3RtIDWcJtxKDHtRgXiuCy1dITSAaEQscv-uz2_7-G5gVWqgQQ9RiFGMcFPzwS94DCO4gCsnEdjzp3vIL8rIwdTivdq5dcKncKWUG03pjNH33JHde4OJh14ygaJ2bHUecg_0vhLV0uJppn3e0KL0x91O0RdhqieeI14UUesKHCGWM83tR_xT8U-BapfD25HIIBJtAqSMID-V8ytheTmwYv3rFbND0pe1qHx_gCuahGNWMRxVpdu88MounMj4X7_B5MISRE.Dt1iLQ.2RTdiMilb_0f9nPjCIlZa6UL2G0
len(soups)

In [ ]:
soups[42]

In [ ]:
#takes EC projectID line as an input, returns only the 6 digit EC project code
def getProjectCode(totalstring):
    splitted = totalstring.split('/')
    result = str(splitted[len(splitted)-2])
    return result;

In [ ]:
def getOutputlist(records):
    nodelist = list()
    for record in records:
        for sibling in record.previous_siblings:
            if sibling.name == 'dc:date':
                recorddate = sibling.text #need to parse the date
            if sibling.name == 'dc:identifier':
                recordID = sibling.text
            #if sibling.name == 'dc:rights':
                #if 'eu-repo' not in sibling.text:
            #    tempo = sibling.text
            if 'grantAgreement' in record.text:
                grantID = record.text
        for sibling in record.next_siblings:
            if sibling.name == 'dc:type':
                recordtype = sibling.text #need to parse the date
        #append row to nodelist - recordID, related grant, date
        nodelist.append([recordID, grantID, recorddate, recordtype])
        print "record: ", recordID, grantID, recorddate, recordtype
    return nodelist;
#edgelist
#nodelist

In [ ]:
#FOR ZENODO
#gets a list of soups, finds relation tags and produces a list of outputs in the form of outputID, grantID, output date, output type
totaloutputlist = list()
for soup in soups:
    souprecords = soup.find_all(re.compile("^dc:relation"), string=re.compile("grantAgreement"))
    outputlist = getOutputlist(souprecords)
    totaloutputlist = totaloutputlist + outputlist
print len(totaloutputlist)

In [ ]:
# convert output list into nodelist
# for this need to take list of outputs and add to list of unique grantIDs
# assign "grant" type to grantID rows
def outstonodelist(outputlist):
    nodelist = list()
    for output in outputlist:
        #add all outputID, date, type columns to the node list
        nodelist.append([output[0],output[2],output[3]])
        #add grantID with date and type "grant"
        
    print nodelist

In [ ]:
outstonodelist(totaloutputlist)

## OpenAire below is limited to 10000 records

In [ ]:
#get list of FP7 and H2020 projects with dates
#http://api.openaire.eu/search/projects?page=2&size=1000&startYear=2010
testyear = '2011'
#aireresp = requests.get('http://api.openaire.eu/search/projects?page=1&size=1000&startYear=2011')
#airesoup = BeautifulSoup(aireresp.content, 'lxml')
#airesoup

In [ ]:
#get a soup list for open aire
airesoups = list()
maxpages = 11
for i in range(1, maxpages):
    print i,"/", maxpages
    requestring = 'http://api.openaire.eu/search/projects?page=' + str(i) + '&size=1000&startYear=' + testyear
    print requestring
    resploop = requests.get(requestring)
    souploop = BeautifulSoup(resploop.content, 'lxml')
    airesoups.append(souploop)
    #print currecords,"/",maxrecords

In [ ]:
#FOR OPENAIRE
#continue with the soup list
#for each soup
    #get 'code' tags for the soup
    #for each codetag/record
        #attach to dict with date
grantdict = dict()
recorddate = ''
for airesoup in airesoups:
    souprecords = airesoup.find_all('code')
    #take records get nodelist and edgelist
    for record in souprecords:
        for sibling in record.previous_siblings:
            if sibling.name == 'startdate':
                recorddate = sibling.text #need to parse the date
            #grantlist.append([record.text, recorddate])
        grantdict[record.text] = recorddate
        #print len(grantdict)
        #print "record", record.text, recorddate
len(grantdict)

## BELOW CODE IS NOT USED FOR NOW

In [ ]:
#while page < max, use resumptiontokens to extract soups, then put all data into one big soup?
#resptwo = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=2544493|oaf|*%20AND%20oaftype%20exact%20"project"|1000|5beebb231e82123b9ba6b95d|false|projects')
#get resumptiontoken
#session = requests.session()
#session.keep_alive = False
soups = list()
soups.append(soupec)
restoken = soupec.find(re.compile("^oai:resumptiontoken"))
print restoken.text
maxrecords = getMaxRecords(restoken.text)
currecords = getCurrentRecords(restoken.text)
#while currecords < maxrecords:
for i in range(2000, int(maxrecords)+2000, 1000):
    print currecords,"/",maxrecords
    newtoken = getGoodToken(restoken.text)
    print "newtoken:", newtoken
    requestring = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=' + newtoken
    resploop = requests.get(requestring)
    #print "resploop:", resploop.content
    souploop = BeautifulSoup(resploop.content, 'lxml')
    soups.append(souploop)
    restoken = souploop.find(re.compile("^oai:resumptiontoken"))
    print restoken
    #extract max and currently shown records
    maxrecords = getMaxRecords(restoken.text)
    currecords = getCurrentRecords(restoken.text)
    #print currecords,"/",maxrecords

In [ ]:
soups[6]

In [ ]:
restoken = soups[len(soups)-3].find(re.compile("^oai:resumptiontoken"))
print restoken.text
newtoken = getGoodToken(restoken.text)
print "newtoken:", newtoken
requestring = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=' + newtoken
resploop = requests.get(requestring)
#print "resploop:", resploop.content
souploop = BeautifulSoup(resploop.content, 'lxml')
soups.append(souploop)
restoken = souploop.find(re.compile("^oai:resumptiontoken"))
print restoken

In [ ]:
respectest = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=45444|oaf|*%20AND%20(oaftype%20exact%20"project"%20and%20funder%20exact%20"EC")|7000|5beebcd3b531c539006a066d|false|ECProjects')
respectest.content

In [ ]:
#takes resumption token string as an input, returns part before the first separator
def getMaxRecords(totalstring):
    splitted = totalstring.split('|')
    #print splitted[0]
    #result = str(splitted[len(splitted)-2])
    return splitted[0];

In [ ]:
#takes resumption token string as an input, returns part before the first separator
def getCurrentRecords(totalstring):
    splitted = totalstring.split('|')
    #print splitted[0]
    #result = str(splitted[len(splitted)-2])
    return splitted[3];

In [ ]:
def getCursor(restoken):
    result = restoken['cursor']
    return result;

In [20]:
#NOT USED, uses dictionary
#takes a filename with soup inside, retrives grantIDs and respective date
def getGrantFromFile(filename):
    grantdict = dict()
    with open(filename) as file:  
        #restoken = file.readlines()[-2]
        #print restoken
        tempstr = file.read()
        #print tempstr
        soup = BeautifulSoup(tempstr, 'lxml')
        grantIDtags = soup.find_all('code')
        for grantID in grantIDtags:
            #print grantID
            grantIDdate = 'not available'
            for sibling in grantID.previous_siblings:
                if sibling.name == 'startdate':
                    grantIDdate = sibling.text #need to parse the date
            for sibling in grantID.next_siblings:
                if sibling.name == 'startdate':
                    grantIDdate = sibling.text #need to parse the date
            grantdict[grantID.text] = grantIDdate
    return grantdict
    #print len(grantdict)
    #print grantdict

In [ ]:
#for each record
    #find siblings with date
    #put record + date into grantdict
grantdict = dict()
for record in recordstwo:
    for sibling in record.previous_siblings:
        if sibling.name == 'startdate':
            recorddate = sibling.text #need to parse the date
    #grantlist.append([record.text, recorddate])
    grantdict[record.text] = recorddate
    #print "record", record.text
grantdict

In [ ]:
#retrieve projects from openaire
#build a 2d list in the form of grantID - date
#get first request
resptwo = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&set=projects&metadataPrefix=oaf')
#NOTE: size is set to 1000 by default
#TODO: retrieve resumption token, put in loop
souptwo = BeautifulSoup(resptwo.content, 'lxml')
#http://api.openaire.eu/oai_pmh?verb=ListRecords&set=projects&metadataPrefix=oaf
souptwo

In [ ]:
temp = '2544493|oaf|* AND oaftype exact "project"|1000|5beebb231e82123b9ba6b95d|false|projects'
       '2544493|oaf|* AND oaftype exact "project"|1000|5beebb231e82123b9ba6b95d|false|projects'
newtemp = temp.replace(' ', '%20')
newtemp

In [ ]:
#get list of project codes
recordstwo=souptwo.find_all('code')

In [ ]:
#get a list of all objects with ID and http links (the other ones are repeating - e.g. oai)
#records=soup.find_all(re.compile("^dc:identifier"), string=re.compile("http"))
records=soup.find_all(re.compile("^dc:identifier"))

In [ ]:
#clean records - leave only doi identifiers
#WHY this needs two times execution?
for record in records:
    if ("http" in record.text) or ("oai:" in record.text):
        records.remove(record)
        print record.text,' removed'
records

In [ ]:
getProjectCode('info:eu-repo/grantAgreement/EC/FP7/603264/')

In [ ]:
grantdict['248919']

In [ ]:
root = ET.fromstring(resp.content)

In [ ]:
print(root.findall('.//*'))

In [ ]:
print root.findall('{http://purl.org/dc/elements/1.1/}relation')

In [ ]:
dc = 'http://purl.org/dc/elements/1.1/'
print root.find('{http://purl.org/dc/elements/1.1}relation')

In [ ]:
print(ET.tostring(root, encoding='utf8').decode('utf8'))

In [ ]:
#listRecords, record, metadata, dc, relation
#root[2][0][1][0][11].text
#for index in range(0, 90):
    #print(root[2][index][1][0][11].text)
print(root[2][0][1][0][11].text)
print(root[2][1][1][0][11].text)
    #print(root[2][index][1][0][7].text)

In [ ]:
for relation in root.iter('dc%3Arelation'):
    print(relation.attrib)

In [ ]:
for record in root[2].iter('relation'):
    print record.attrib

In [ ]:
getCurrentRecords(u'2544493|oaf|* AND oaftype exact "project"|2000|5beebb23be047061a7690bc3|false|projects')

In [ ]:
getGoodToken(u'2544493|oaf|* AND oaftype exact "project"|2000|5beebb23be047061a7690bc3|false|projects')